In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import pickle, pandas as pd, pmdarima as pmd, geopandas as gpd,numpy as np
from random import choice
import crf_utilities_again as crf_util
import xarray as xr, geopandas as gpd, rioxarray, os
from shapely.geometry import box, mapping
import geopandas as gpd
import matplotlib.pyplot as plt

In [5]:
regions_all = gpd.read_file(
    '/home/gchossie/2020_aq/monitor_based/data/all_regions.geojson')

In [6]:
results_geo = regions_all.copy()

In [ ]:
results_geo

In [7]:
for col in ['NO2 mean', 'NO2 2.5', 'NO2 97.5',
            'PM2.5 mean', 'PM2.5 2.5', 'PM2.5 97.5',
             'O3 mean', 'O3 2.5', 'O3 97.5']:
    results_geo.loc[:,col] = 0

In [8]:
results_geo.reset_index(drop=True,inplace=True)

In [7]:
results_geo.head(3)

Ensemble Country    Region  Population  \
0    Japan   Japan     Aichi   7220143.5   
1    Japan   Japan     Osaka   8177242.0   
2    Japan   Japan  Shizuoka   3460957.0   

                                            geometry  NO2 mean  NO2 2.5  \
0  MULTIPOLYGON (((137.09523 34.65330, 137.09546 ...         0        0   
1  MULTIPOLYGON (((135.31573 34.43310, 135.31544 ...         0        0   
2  MULTIPOLYGON (((141.46085 24.24579, 141.46115 ...         0        0   

   NO2 97.5  PM2.5 mean  PM2.5 2.5  PM2.5 97.5  O3 mean  O3 2.5  O3 97.5  
0         0           0          0           0        0       0        0  
1         0           0          0           0        0       0        0  
2         0           0          0           0        0       0        0

In [9]:
raw_dist = {}

In [10]:
N = 10000
samples = np.random.normal(size=N)
for idx in results_geo.index:
    country = results_geo.loc[idx,'Country']
    reg = results_geo.loc[idx,'Region']
    if country not in raw_dist.keys():
        raw_dist[country] = {reg: {}}
    else:
        raw_dist[country] = {**raw_dist[country], **{reg: {}}}
    for sp in ['O3', 'PM2.5', 'NO2']:
        raw_dist[country][reg][sp] = {}
        for cause in ['Lower respiratory infections',
                      'Upper respiratory infections',
                      'Chronic respiratory diseases',
                      'Cardiovascular diseases',
                      'All causes']:
            mort = crf_util.get_mort(country, reg, sp, cause='All causes', scen='', 
                                     samples=samples, method='kriging', sens=True, 
                                     counterfactual=False)
            if mort is None: 
                raw_dist[country][reg][sp][cause] = 0 
                continue
            else:
                raw_dist[country][reg][sp][cause] = mort
        try:
            results_geo.loc[idx,f'{sp} mean'] = mort.mean()
            results_geo.loc[idx,f'{sp} 2.5'] = np.percentile(mort,2.5)
            results_geo.loc[idx,f'{sp} 97.5'] = np.percentile(mort,97.5)
        except: pass

In [ ]:
results_geo.loc[results_geo.Region == 'Massachusetts',:]

In [ ]:
results_geo['NO2 mean'].sum() + results_geo['PM2.5 mean'].sum() + results_geo['O3 mean'].sum() 

In [ ]:
ctr = 'United States'; sp = 'PM2.5'
regs = list(set(results_geo.loc[results_geo.Country == ctr, 'Region']))
np.percentile(np.sum([raw_dist[ctr][reg][sp] for reg in regs], axis=0),[2.5, 50, 97.5])

In [ ]:
results_geo.loc[results_geo.Country == ctr, 'NO2 mean'].sum()

In [ ]:
sp = 'PM2.5'
np.percentile(np.sum([raw_dist[results_geo.loc[idx,'Country']][results_geo.loc[idx,'Region']][sp] for idx in results_geo.index], axis=0),50)

In [ ]:
results_geo.to_file('./results/result_moni_mort_oct_15.geojson',driver='GeoJSON')
#results_geo.to_file('./results/result_moni_mort_jul9_counterfactual.geojson',driver='GeoJSON')

In [11]:
with open('./results/raw_mort_dist_oct_21_sens.pkl','wb') as f:
    pickle.dump(raw_dist,f)
#with open('./results/raw_mort_dist_jul9_counterfactual.pkl','wb') as f:
#    pickle.dump(raw_dist,f)